# SnowEnergyBalance Component Tutorial
(Tian Gan, Sept 2023)

This tutorial demonstrates how to use the SnowEnergyBalance component to simulate the snow accumulation and snowmelt process for a study area in Colorado. It includes the following sections:

- Component introduction
- Prepare model inputs
- Model simulation
- Results analysis

## Component introduction

**SnowEnergyBalance** component accounts for energy fluxes (e.g., short wave radiation, long wave radiation, sensible heat, latent heat) to simulate snowpack dynamics. This component uses the net total energy flux (Q_sum) and the snowpack cold content (Ecc) to determine the snowmelt rate with the following logic:

If the net total energy (Q_sum * dt) is larger than Ecc, the melt process starts using the remaining energy (Q_rem = Q_sum*dt - Ecc).
If the net total energy is positive but less than Ecc, the snowpack is warming and the Ecc decrease.
If the total energy is negative, the snow is cooling and the Ecc increase.

$Q\_sum = Qn\_SW + Qn\_LW + Qh + Qe + Qa + Qc$

* Qn_SW: net short wave energy flux
* Qn_LW: net long wave energy flux
* Qh: sensible heat energy flux
* Qe: latent heat energy flux
* Qa: net energy flux advected by moving water (assume this to be negligible; Qa=0)
* Qc: net energy flux via conduction from snow to soil (assume this to be negligible; Qc=0)

$Ecc = rho\_snow * Cp\_snow * (T\_air - T\_surf) * h\_snow$
* rho_snow: snow density
* Cp_snow: snow heat capacity
* T_air: air temperature
* T_surf: snow layer temperature
* h_snow: snow depth

To get an overview of the component, we can examine its *header docstring*, which is the internal documentation provided in the form of a Python docstring that sits just below the class declaration in the source code:

In [ ]:
from landlab.components import SnowEnergyBalance

print(SnowEnergyBalance.__doc__)

Now, let's check about the input and output data fields for this component. 

In [ ]:
# input
SnowEnergyBalance.input_var_names

In [ ]:
# optional input
SnowEnergyBalance.optional_var_names

In [ ]:
# output
SnowEnergyBalance.output_var_names

In [ ]:
# units
SnowEnergyBalance.units

## Prepare model inputs

We choose the Gunnison River Basin in Colorado as the study area with the bounding box of [-109.0, 39.5, -106, 37.5]. (Image source: https://gunnisonriverbasin.org/water-plans-management/water-management/).

We will use [ERA5 Data Component](https://csdms.colorado.edu/wiki/Model:ERA5_Data_Component) to access hourly datasets with grid resolution of ~31km for May 1-7, 2023. The variables downloaded include:
- air temperature
- temperature of snow layer
- snow depth (in water equivalent)
- total precipitation
- mean surface latent heat flux
- mean surface sensible heat flux
- mean surface net short-wave radiation flux
- mean surface net long-wave radiation flux



### Download datasets
For the ERA5 Data Component, there is a need to create an API key file to download the datasets. If you didn't install this file, you can uncomment the code in the cell below and run them. The install_api_key( ) function will ask for your [CDS API Key](https://cds.climate.copernicus.eu/api-how-to) to create an API key file. Please make sure you have already obtained the API Key before you run this helper function.

In [ ]:
# # install api key
# from utils import install_api_key

# install_api_key()

In [ ]:
# initialize ERA5 data component
from pymt.models import Era5

era5 = Era5()
era5.initialize("era5_config_seb.yaml")

In [ ]:
# plot ERA5 dataset (at the first time step)
from matplotlib import pyplot as plt

fig = plt.figure(figsize=(12, 14))
nrows, ncols = 4, 2
i = 1

for var_name in era5.output_var_names:
    ax = fig.add_subplot(nrows, ncols, i)
    var_unit = era5.var_units(var_name)

    # get variable data
    era5_data = era5.get_value(var_name)
    era5_data_2D = era5_data.reshape(era5.grid_shape(0))

    # plot data
    im = ax.imshow(era5_data_2D, cmap="Blues")
    ax.title.set_text(f"{var_name} ({var_unit})")
    cbar = plt.colorbar(im, ax=ax)

    i += 1

### Define model grid 

We will first define a RasterModelGrid for the study area. The model grid shape will be the same as the ERA5 datasets. Then, we will assign the ERA5 datasets as the input data fields. The mean energy flux variables from ERA5 will be used to calculate the net total energy flux for `land_surface_net-total-energy__energy_flux` data field (Since Qa and Qc are very small values, we suppose they are 0.) Also, we will use the snow depth (in water equivalent) at the first time step from ERA5 as the initial input for `snowpack__liquid-equivalent_depth`. This initial snow depth input will be used for model analysis in the later section.

In [ ]:
from landlab import RasterModelGrid

grid = RasterModelGrid(era5.grid_shape(0), xy_spacing=(31000, 31000))

In [ ]:
# add air temperature field
T_air = grid.add_zeros("atmosphere_bottom_air__temperature", at="node", clobber=True)
T_air[:] = era5.get_value("2 metre temperature") - 273.15  # units: K to C

In [ ]:
# add snow surface temperature field
T_surf = grid.add_zeros("land_surface__temperature", at="node", clobber=True)
T_surf[:] = era5.get_value("Temperature of snow layer") - 273.15  # units: K to C

In [ ]:
# add precipitation field
P = grid.add_zeros(
    "atmosphere_water__precipitation_leq-volume_flux", at="node", clobber=True
)
P[:] = era5.get_value("Total precipitation") / 3600  # units: m/hr to m/s

In [ ]:
# add net total energy flux field
Qn_SW = era5.get_value("Mean surface net short-wave radiation flux")
Qn_LW = era5.get_value("Mean surface net long-wave radiation flux")
Qe = era5.get_value("Mean surface latent heat flux")
Qh = era5.get_value("Mean surface sensible heat flux")

Q_sum = grid.add_zeros(
    "land_surface_net-total-energy__energy_flux", at="node", clobber=True
)
Q_sum[:] = Qn_SW + Qn_LW + Qe + Qh

In [ ]:
# add initial snow water equivalent
h_swe = grid.add_zeros("snowpack__liquid-equivalent_depth", at="node", clobber=True)
h_swe[:] = era5.get_value("Snow depth")

In [ ]:
# store the initial swe for results analysis
init_swe = era5.get_value("Snow depth").copy()

## Model simulation

We will initialize an instance for SnowEnergyBalance component. The simulation time will be 168hr (May 1-7, 2023) and the time step is 1hr. At each time step, we will update the input for air temperature, land surface temperature, precipitation, and net total energy flux. 

In [ ]:
# initialize an instance
seb = SnowEnergyBalance(grid)

In [ ]:
# show parameters, constants and data fields
print(
    f"\nwater density: {seb.rho_H2O}",
    f"\nair density: {seb.rho_air}",
    f"\nair heat capacity: {seb.Cp_air}",
    f"\ntemperature threshold for rain and snow: {seb.T_rain_snow}",
    f"\ngrid area: {seb.grid_area}",
    f"\nlatent heat of vaporization: {seb.Lv}",
)

grid.at_node.keys()

In [ ]:
# run model
from tqdm import trange

dt = 3600  # sec
time_steps = 167

for time_step in trange(0, time_steps):
    # run model
    seb.run_one_step(dt)

    # update input
    if time_step < time_steps - 1:
        # update dataset
        era5.update()

        # assign input fields
        P[:] = era5.get_value("Total precipitation") / 3600  # units: m/hr to m/s
        T_air[:] = era5.get_value("2 metre temperature") - 273.15  # units: K to C
        # T_surf[:] = era5.get_value("Temperature of snow layer") - 273.15

        Qn_SW = era5.get_value("Mean surface net short-wave radiation flux")
        Qn_LW = era5.get_value("Mean surface net long-wave radiation flux")
        Qe = era5.get_value("Mean surface latent heat flux")
        Qh = era5.get_value("Mean surface sensible heat flux")
        Q_sum[:] = Qn_SW + Qn_LW + Qe + Qh

## Results analysis

Now, let's make some plots for the results. We will compare the initial SWE at the first time step with the simulated SWE and the ERA5 SWE data at the last time step. From the plot, you will find that the snowmelt pattern are very similar between the simulated SWE and the ERA5 data.

In [ ]:
fig = plt.figure(figsize=(18, 10))
nrows, ncols = 2, 2
i = 1

sim_swe = grid.at_node["snowpack__liquid-equivalent_depth"]
era5_swe = era5.get_value("Snow depth")
diff_swe_sim = init_swe - sim_swe
diff_swe_era5 = init_swe - era5_swe

plot_data = [
    era5_swe,
    sim_swe,
    diff_swe_era5,
    diff_swe_sim,
]
titles = [
    "ERA5 SWE",
    "SnowEnergyBalance SWE",
    "SWE Difference ERA5",
    "SWE Difference SDD",
]
for title, data in zip(titles, plot_data):
    ax = fig.add_subplot(nrows, ncols, i)

    # get variable data
    data_2D = data.reshape(era5.grid_shape(0))

    # plot data
    im = ax.imshow(
        data_2D, cmap="Blues", vmax=0.12 if "SWE Difference" in title else 0.4
    )
    ax.title.set_text(title)
    cbar = plt.colorbar(im, ax=ax)

    i += 1